# T-Mon: Traces Monitor in xAPI-SG, with SIMVA integration

### T-Mon is a set of Jupyter Notebooks to process, analyze and present visualizations of data following the Experience API for Serious Games Profile (xAPI-SG)

The following code:
- expects as input a **JSON file with a list of xAPI-SG statements, obtained from SIMVA**
- **analyzes the xAPI-SG statements** and fills an adaptation of the **default set of visualizations**
https://github.com/e-ucm/rage-analytics/wiki/Default-visualizations-teacher

For more information, see **T-Mon GitHub page: https://github.com/e-ucm/t-mon**



**xAPI-SG main reference:**
*Applying standards to systematize learning analytics in serious games.
Ángel Serrano-Laguna, Iván Martínez-Ortiz, Jason Haag, Damon Regan, Andy Johnson, Baltasar Fernández-Manjón
Computer Standards & Interfaces 50 (2017) 116–123, http://dx.doi.org/10.1016/j.csi.2016.09.014*

Further info on GitHub wiki page: https://github.com/e-ucm/rage-analytics/wiki/xAPI-SG-Profile

Further info about SIMVA on: https://github.com/e-ucm/simva-infra

## SIMVA connection parameters 

### Defined in *ipyauth-keycloak-demo.env* file:

- `base_url`: URL pointing to SIMVA's SSO service (default: https://sso.simva.e-ucm.es)
- `realm`: simva
- `response_type`: id_token token
- `client_id`: SIMVA's client used by jupyter (e.g. jupyter)
- `redirect_uri`: jupyter URL (e.g. http://localhost:8888/callback/)

### After running the following cell, click on "Sign in" to enter your SIMVA credentials

In [ ]:
import json
import requests as rq

from ipyauth import Auth, ParamsKeycloak

p = ParamsKeycloak(dotenv_file='ipyauth-keycloak-demo.env',
                   scope='profile openid email')
a = Auth(params=p)
a

## SIMVA storage parameters

- `simva_storage_url`: URL pointing to SIMVA storage service (default: https://minio.simva.e-ucm.es)
- `simva_ca_file`: if SIMVA is installed locally this should point to a file with the CA certificate used by simva (usually located at `$SIMVA_HOME/docker-stacks/data/tls/ca/rootCA.pem`), `None` otherwise

In [ ]:
simva_storage_url = 'https://minio.simva.e-ucm.es'
simva_ca_file = None

local = True # Set to True if working with a local-hoster Jupyter server, False if working with a web-hosted Jupyter server
storage = 'simva'

import json
import numpy as np
from datetime import datetime, timedelta
import copy
import math
import matplotlib.dates as mdates
import matplotlib.pyplot as plt
from collections import Counter
import pandas as pd
from ipywidgets import interact, interactive, fixed, HBox, Layout,VBox
import ipywidgets as widgets
from IPython.display import display, clear_output
import pprint
plt.style.use('default')

***Display all* function** is constructing an app to display all vis

In [ ]:
players_info = {} # dict with players info
global timeformats
timeformats=['%Y-%m-%dT%H:%M:%SZ','%Y-%m-%dT%H:%M:%S.%fZ'] #array of time format

%run fileBrowserAndUploadButtonToLoadProcessStatements.ipynb
%run vis/helpersFunctions/clearFigMatplotlib.ipynb
%run globalsSelectors.ipynb

header=widgets.HTML("<h1>xAPI-SG Processor</h1> <h2>Please select .json xAPI SG file to process this file and see visualisations</h2>")
footer=widgets.HTML("<h4>xAPI-SG Processor, by eUCM research team</h4>")
if storage == 'simva' :
    app=VBox([header,simvaWidget.widget(),footer])
    display(app)
else:
    if local:
        app=VBox([header,fileBrowser.widget(),footer])
        display(app)
    else:
        app=VBox([header,uploadButtonApp,footer])
        display(app)
        with outTabs:
            display_checkboxes()
            clear_output(wait=True)
        displayvis(None)